In [ ]:
from datetime import datetime as dt
from collections import namedtuple
from pathlib import Path

from toargridding.toar_rest_client import AnalysisService
from toargridding.grids import RegularGrid
from toargridding.gridding import get_gridded_toar_data
from toargridding.metadata import TimeSample

In [ ]:
#creation of request.

Config = namedtuple("Config", ["grid", "time", "variables", "stats"])

valid_data = Config(
    RegularGrid( lat_resolution=1.9, lon_resolution=2.5, ),
    TimeSample( start=dt(2014,1,1), end=dt(2019,12,31), sampling="daily"),
    ["mole_fraction_of_ozone_in_air"],#variable name
    ["mean"]# ["dma8epax"], # enable when finished
)
missing_data = Config(
    RegularGrid( lat_resolution=1.9, lon_resolution=2.5),
    TimeSample( start=dt(2000,1,1), end=dt(2013,12,31), sampling="daily"),
    ["mole_fraction_of_ozone_in_air"],
    ["dma8epax"],
)

configs = {
    "test_ta": valid_data
}

#testing access:
config = configs["test_ta"]
config.grid

In [ ]:
#CAVE: this cell runs about 30minutes per requested year
#the processing is done on the server of the TOAR database.
#a restart of the cell continues the request to the REST API if the requested data are ready for download
# The download can also take a few minutes

stats_endpoint = "https://toar-data.fz-juelich.de/api/v2/analysis/statistics/"
result_basepath = Path("results")
result_basepath.mkdir(exist_ok=True)
analysis_service = AnalysisService(stats_endpoint, result_basepath)

for person, config in configs.items():
    datasets, metadatas = get_gridded_toar_data(
        analysis_service=analysis_service,
        grid=config.grid,
        time=config.time,
        variables=config.variables,
        stats=config.stats
    )

    for dataset, metadata in zip(datasets, metadatas):
        dataset.to_netcdf(result_basepath / f"{metadata.get_id()}.nc")
        print(metadata.get_id())